In [28]:
import pandas as pd 
dataset = pd.read_csv("data/hackerank/combined_data.csv")
import ast

def clean_tags(tag_string):
    # Convert the string to a list
    tag_list = ast.literal_eval(tag_string)
    # Join the list into a comma-separated string
    return ', '.join(tag_list)

dataset['Tags']=dataset['Tags'].apply(clean_tags)

In [29]:
df = dataset

In [30]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.preprocessing import LabelEncoder

def vectorirse_text(text):
    """ Recieves text as input and returns TF-IDF vectors"""
    tfidf = TfidfVectorizer(max_features=500000)
    X = tfidf.fit_transform(text)
    return X

def label_encoding(input):
    label_encoder = LabelEncoder()
    return label_encoder.fit_transform(input)


X = vectorirse_text(df['Input'])
y = label_encoding(df['Tags'])

In [31]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix

# Assuming df is already loaded
# And vectorise_text and label_encoding are already available

# Step 1: Preprocess
# X = vectorise_text(df['text'])
# y = label_encoding(df['label'])

# Step 2: Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Step 3: Train Logistic Regression
model = LogisticRegression(max_iter=1000)
model.fit(X_train, y_train)

# Step 4: Predict on the test set
y_preds = model.predict(X_test)

# Step 5: Evaluate
acc = accuracy_score(y_test, y_preds)
print(f"✅ Accuracy on Test Set: {acc:.4f}\n")

print("✅ Classification Report on Test Set:\n")
print(classification_report(y_test, y_preds))

print("✅ Confusion Matrix on Test Set:\n")
print(confusion_matrix(y_test, y_preds))

# ----------------------------
# Step 6: Predict probabilities for FULL fX
# ----------------------------

# Assuming fX and fy are available (full dataset for probability generation)
# fX = vectorise_text(df_full['text'])
# fy = label_encoding(df_full['label'])

y_proba = model.predict_proba(X)

# Step 7: Save probabilities
proba_df = pd.DataFrame(y_proba, columns=[f'class_{i}' for i in range(y_proba.shape[1])])
proba_df.insert(0, 'y_true', y)

proba_df.to_csv('Phase1/TFIDF.csv', index=False)

print("✅ Saved probabilities to Phase1/TFIDF.csv successfully!")
proba_df.head()


✅ Accuracy on Test Set: 0.9124

✅ Classification Report on Test Set:

              precision    recall  f1-score   support

           0       0.95      0.90      0.92       792
           1       0.86      0.85      0.85       709
           2       0.92      0.93      0.92       729
           3       0.94      0.94      0.94       830
           4       0.92      0.86      0.89       486
           5       0.94      0.94      0.94       680
           6       0.94      0.99      0.96       803
           7       0.85      0.88      0.86       634
           8       0.83      0.85      0.84       704
           9       0.97      0.95      0.96       684

    accuracy                           0.91      7051
   macro avg       0.91      0.91      0.91      7051
weighted avg       0.91      0.91      0.91      7051

✅ Confusion Matrix on Test Set:

[[711  22   8   4   0   7   4  22  12   2]
 [ 12 604   8   3   2  10   5  12  51   2]
 [  7   2 679   5   7   7   8   8   6   0]
 [  1   6

y_true   class_0   class_1   class_2   class_3   class_4   class_5  \
0       2  0.004856  0.009864  0.864422  0.008940  0.009183  0.016639   
1       2  0.005297  0.006558  0.913401  0.006262  0.011597  0.018983   
2       2  0.030078  0.035363  0.681136  0.038987  0.025477  0.060935   
3       2  0.014440  0.015472  0.790973  0.023952  0.023529  0.020345   
4       2  0.012646  0.019750  0.612334  0.116218  0.036532  0.027983   

    class_6   class_7   class_8   class_9  
0  0.039277  0.026571  0.010824  0.009424  
1  0.018909  0.006744  0.009302  0.002946  
2  0.024796  0.033198  0.045627  0.024402  
3  0.037677  0.027091  0.030567  0.015954  
4  0.045918  0.060600  0.036102  0.031918

35251

In [32]:
import gensim
import numpy as np
from sklearn.ensemble import RandomForestClassifier

df['tokens'] = df['Input'].apply(lambda x: x.split())

w2v_model = gensim.models.Word2Vec(sentences=df['tokens'], vector_size=10000, window=5, min_count=2, workers=10)

def get_sentence_embedding(tokens):
    vectors = [w2v_model.wv[word] for word in tokens if word in w2v_model.wv]
    return np.mean(vectors, axis=0) if vectors else np.zeros(100)

X_w2v = np.array(df['Input'].apply(get_sentence_embedding).tolist())
y_encoded = label_encoding(df['Tags'])


In [33]:
X = X_w2v
y = y_encoded

In [34]:
import xgboost as xgb
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
import pandas as pd
import os

# Step 1: Ensure Phase1 folder exists
os.makedirs('Phase1', exist_ok=True)

# Step 2: Train-test split
X_train, X_test, y_train, y_test = train_test_split(X_w2v, y_encoded, test_size=0.2, random_state=42)

# Step 3: Train XGBoost model
model = xgb.XGBClassifier(use_label_encoder=False, eval_metric='mlogloss')
model.fit(X_train, y_train)

# Step 4: Predict on the test set
y_preds = model.predict(X_test)

# Step 5: Evaluate
acc = accuracy_score(y_test, y_preds)
print(f"✅ Accuracy on Test Set: {acc:.4f}\n")

print("✅ Classification Report on Test Set:\n")
print(classification_report(y_test, y_preds))

print("✅ Confusion Matrix on Test Set:\n")
print(confusion_matrix(y_test, y_preds))

# ---------------------------------
# Step 6: Predict probabilities on full data
# ---------------------------------
y_proba = model.predict_proba(X_w2v)

proba_df = pd.DataFrame(y_proba, columns=[f'class_{i}' for i in range(y_proba.shape[1])])
proba_df.insert(0, 'y_true', y_encoded)

proba_df.to_csv('Phase1/Word2Vec_Proba.csv', index=False)

print("\n✅ Also saved class probabilities to Phase1/Word2Vec_Proba.csv!")
proba_df.head()


/home/darth/.pyenv/versions/major02/lib/python3.10/site-packages/xgboost/training.py:183: UserWarning: [20:55:48] WARNING: /workspace/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)


✅ Accuracy on Test Set: 0.3624

✅ Classification Report on Test Set:

              precision    recall  f1-score   support

           0       0.36      0.37      0.36       792
           1       0.23      0.21      0.22       709
           2       0.35      0.31      0.33       729
           3       0.36      0.42      0.39       830
           4       0.46      0.36      0.40       486
           5       0.37      0.33      0.35       680
           6       0.46      0.62      0.53       803
           7       0.29      0.27      0.28       634
           8       0.31      0.24      0.27       704
           9       0.40      0.44      0.42       684

    accuracy                           0.36      7051
   macro avg       0.36      0.36      0.35      7051
weighted avg       0.36      0.36      0.36      7051

✅ Confusion Matrix on Test Set:

[[293  69  53  87  15  55  61  51  49  59]
 [119 150  63 103  22  43  52  58  54  45]
 [ 74  80 225  73  20  55  64  53  50  35]
 [ 62  65

y_true   class_0   class_1   class_2   class_3   class_4   class_5  \
0       2  0.001849  0.025684  0.877031  0.003476  0.035381  0.001487   
1       2  0.015427  0.064957  0.766613  0.013290  0.003748  0.015020   
2       2  0.002920  0.028854  0.895788  0.003870  0.001294  0.027167   
3       2  0.042182  0.080883  0.610961  0.017962  0.013955  0.062833   
4       2  0.047361  0.035454  0.254978  0.578128  0.000258  0.002649   

    class_6   class_7   class_8   class_9  
0  0.005956  0.028449  0.009045  0.011643  
1  0.071054  0.031261  0.015151  0.003479  
2  0.016574  0.002937  0.015733  0.004863  
3  0.094489  0.048541  0.008779  0.019415  
4  0.003503  0.044763  0.030260  0.002646

In [13]:
proba_df.to_csv('Phase1/Word2Vec.csv', index=False)

In [35]:
import numpy as np
import gensim.downloader as api

# Load Pretrained GloVe Model
glove_model = api.load("glove-wiki-gigaword-300")  

# Convert a sentence to a vector by averaging word embeddings
def get_sentence_embedding(sentence, model, dim=300):
    words = sentence.split()
    word_vectors = [model[word] for word in words if word in model]
    return np.mean(word_vectors, axis=0) if word_vectors else np.zeros(dim)

text_samples = ["GloVe embeddings capture word semantics"]
embeddings = np.array([get_sentence_embedding(text, glove_model) for text in text_samples])


from tqdm import tqdm

# Generate GloVe embeddings for the entire dataset with a progress bar
df['glove_embeddings'] = df['Input'].apply(lambda x: get_sentence_embedding(x, glove_model))

# Convert the list of embeddings to a numpy array
X_glove = np.array([get_sentence_embedding(text, glove_model) for text in tqdm(df['Input'], desc="Generating GloVe Embeddings")])

# Check the shape of the generated embeddings
print(X_glove.shape)

Generating GloVe Embeddings: 100%|██████████| 35251/35251 [00:01<00:00, 22919.42it/s]

(35251, 300)


In [36]:
X = df['glove_embeddings']
y = label_encoding(df['Tags']) 


In [37]:
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
import pandas as pd
import os
import numpy as np

# Step 0: Ensure Phase1 folder exists
os.makedirs('Phase1', exist_ok=True)

# Step 1: Fix X if needed
if isinstance(X.iloc[0], np.ndarray):
    X = np.vstack(X.values)

# Step 2: Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Step 3: Train SVM model
model = SVC(kernel='linear', probability=True)
model.fit(X_train, y_train)

# Step 4: Predict on the test set
y_preds = model.predict(X_test)

# Step 5: Evaluate
acc = accuracy_score(y_test, y_preds)
print(f"✅ Accuracy on Test Set: {acc:.4f}\n")

print("✅ Classification Report on Test Set:\n")
print(classification_report(y_test, y_preds))

print("✅ Confusion Matrix on Test Set:\n")
print(confusion_matrix(y_test, y_preds))

# ---------------------------------
# Step 6: Predict probabilities on full data
# ---------------------------------
y_proba = model.predict_proba(X)

# Step 7: Save probability scores
proba_df = pd.DataFrame(y_proba, columns=[f'class_{i}' for i in range(y_proba.shape[1])])
proba_df.insert(0, 'y_true', y)

proba_df.to_csv('Phase1/GloVe.csv', index=False)

print("\n✅ Saved probabilities to Phase1/GloVe.csv!")
proba_df.head()


✅ Accuracy on Test Set: 0.7103

✅ Classification Report on Test Set:

              precision    recall  f1-score   support

           0       0.66      0.64      0.65       792
           1       0.45      0.50      0.47       709
           2       0.80      0.79      0.79       729
           3       0.70      0.70      0.70       830
           4       0.72      0.63      0.67       486
           5       0.81      0.83      0.82       680
           6       0.91      0.94      0.93       803
           7       0.68      0.74      0.70       634
           8       0.59      0.53      0.56       704
           9       0.78      0.76      0.77       684

    accuracy                           0.71      7051
   macro avg       0.71      0.71      0.71      7051
weighted avg       0.71      0.71      0.71      7051

✅ Confusion Matrix on Test Set:

[[506 137  14  16   5  24   5  31  42  12]
 [123 354  16  20   7  31  12  37  88  21]
 [ 17  22 575  28  22  25   9  14  14   3]
 [ 19  35

y_true       class_0       class_1   class_2   class_3   class_4   class_5  \
0       2  3.351565e-08  3.210468e-08  0.999735  0.000002  0.000007  0.000002   
1       2  5.428256e-04  5.070415e-05  0.998922  0.000006  0.000039  0.000233   
2       2  1.161756e-03  1.901476e-03  0.992795  0.000341  0.000429  0.000718   
3       2  5.475805e-02  1.380654e-01  0.112860  0.074255  0.013319  0.010117   
4       2  1.400376e-02  7.604539e-02  0.115192  0.251055  0.087261  0.082912   

    class_6   class_7   class_8   class_9  
0  0.000029  0.000017  0.000204  0.000004  
1  0.000101  0.000028  0.000066  0.000011  
2  0.000008  0.000079  0.000842  0.001723  
3  0.116254  0.105238  0.271900  0.103235  
4  0.030533  0.185033  0.074275  0.083690

In [25]:
%pip install transformers

  Using cached transformers-4.51.3-py3-none-any.whl (10.4 MB)
  Using cached requests-2.32.3-py3-none-any.whl (64 kB)
  Using cached PyYAML-6.0.2-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (751 kB)
  Using cached huggingface_hub-0.30.2-py3-none-any.whl (481 kB)
  Using cached tokenizers-0.21.1-cp39-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (3.0 MB)
  Using cached safetensors-0.5.3-cp38-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (471 kB)
  Using cached idna-3.10-py3-none-any.whl (70 kB)
  Using cached certifi-2025.4.26-py3-none-any.whl (159 kB)
  Using cached urllib3-2.4.0-py3-none-any.whl (128 kB)
  Using cached charset_normalizer-3.4.1-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (146 kB)

[notice] A new release of pip is available: 23.0.1 -> 25.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


NameError: name 'label_encoding' is not defined

In [38]:
import torch
import pandas as pd
import numpy as np
from tqdm import tqdm
from transformers import AlbertTokenizer, AlbertModel

# Load ALBERT tokenizer and model
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2")
model = AlbertModel.from_pretrained("albert-base-v2")

# Set device (GPU if available, otherwise CPU)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

# Load your dataset (Ensure df['text'] contains the text data)
# df = pd.read_csv("your_dataset.csv")  # Replace with your dataset file
texts = df["Input"].tolist()

# Function to generate embeddings
def get_albert_embeddings(texts, batch_size=16):
    model.eval()  # Set model to evaluation mode
    embeddings_list = []

    for i in tqdm(range(0, len(texts), batch_size), desc="Processing"):
        batch_texts = texts[i : i + batch_size]
        
        # Tokenize the batch
        inputs = tokenizer(batch_texts, return_tensors="pt", padding=True, truncation=True, max_length=512)
        inputs = {key: val.to(device) for key, val in inputs.items()}  # Move to GPU/CPU
        
        # Get embeddings
        with torch.no_grad():
            outputs = model(**inputs)
        
        # Extract [CLS] token representation (sentence embedding)
        cls_embeddings = outputs.last_hidden_state[:, 0, :].cpu().numpy()
        embeddings_list.append(cls_embeddings)

    return np.vstack(embeddings_list)  # Stack all embeddings

# Generate embeddings for all texts
embeddings = get_albert_embeddings(texts)

Processing: 100%|██████████| 2204/2204 [02:07<00:00, 17.25it/s]


In [39]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.preprocessing import LabelEncoder

def vectorirse_text(text):
    """ Recieves text as input and returns TF-IDF vectors"""
    tfidf = TfidfVectorizer(max_features=500000)
    X = tfidf.fit_transform(text)
    return X

def label_encoding(input):
    label_encoder = LabelEncoder()
    return label_encoder.fit_transform(input)

X = embeddings
y = label_encoding(df['Tags'])

In [40]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
import pandas as pd
import os

# Step 0: Ensure Phase1 folder exists
os.makedirs('Phase1', exist_ok=True)

# Step 1: Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Step 2: Train Logistic Regression on training set
model = LogisticRegression(max_iter=1000)
model.fit(X_train, y_train)

# Step 3: Predict on test set
y_preds = model.predict(X_test)

# Step 4: Evaluate
acc = accuracy_score(y_test, y_preds)
print(f"✅ Accuracy on Test Set: {acc:.4f}\n")

print("✅ Classification Report on Test Set:\n")
print(classification_report(y_test, y_preds))

print("✅ Confusion Matrix on Test Set:\n")
print(confusion_matrix(y_test, y_preds))

# --------------------------------
# Step 5: Predict probabilities on full dataset
# --------------------------------
y_proba = model.predict_proba(X)

# Step 6: Save probabilities
proba_df = pd.DataFrame(y_proba, columns=[f'class_{i}' for i in range(y_proba.shape[1])])
proba_df.insert(0, 'y_true', y)

proba_df.to_csv('Phase1/Albert.csv', index=False)

print("\n✅ Saved class probabilities to Phase1/Albert.csv!")
proba_df.head()


/home/darth/.pyenv/versions/major02/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:465: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


✅ Accuracy on Test Set: 0.7949

✅ Classification Report on Test Set:

              precision    recall  f1-score   support

           0       0.76      0.73      0.74       792
           1       0.66      0.66      0.66       709
           2       0.84      0.82      0.83       729
           3       0.79      0.82      0.80       830
           4       0.79      0.76      0.77       486
           5       0.90      0.92      0.91       680
           6       0.98      0.99      0.98       803
           7       0.73      0.75      0.74       634
           8       0.65      0.63      0.64       704
           9       0.82      0.86      0.84       684

    accuracy                           0.79      7051
   macro avg       0.79      0.79      0.79      7051
weighted avg       0.79      0.79      0.79      7051

✅ Confusion Matrix on Test Set:

[[575  95  18  10   3  12   0  33  28  18]
 [ 84 467  12  11   5  16   1  28  69  16]
 [ 13   9 595  26  26  21   3  12  23   1]
 [  6  15

y_true       class_0       class_1   class_2       class_3   class_4  \
0       2  4.046189e-06  1.673384e-06  0.996728  8.242731e-04  0.002150   
1       2  2.162968e-07  8.667423e-07  0.999940  3.937645e-07  0.000004   
2       2  1.016335e-04  3.334410e-04  0.998280  5.001128e-05  0.000006   
3       2  1.920308e-03  1.006953e-02  0.955455  2.492423e-03  0.006655   
4       2  2.279302e-04  3.630354e-05  0.944598  4.439209e-02  0.002457   

    class_5       class_6       class_7   class_8       class_9  
0  0.000016  2.555716e-07  8.192644e-05  0.000194  8.416093e-09  
1  0.000004  6.603543e-08  2.003625e-07  0.000051  2.772808e-09  
2  0.000730  2.283566e-07  1.428000e-06  0.000497  7.577643e-07  
3  0.000183  3.224371e-04  1.568429e-02  0.006673  5.461269e-04  
4  0.000046  6.339463e-06  7.960528e-03  0.000233  4.337906e-05

## Ensemble

In [41]:
import pandas as pd

# Read the CSV files
tfidf_df = pd.read_csv('Phase1/TFIDF.csv')
word2vec_df = pd.read_csv('Phase1/Word2Vec.csv')
glove_df = pd.read_csv('Phase1/GloVe.csv')
albert_df = pd.read_csv('Phase1/Albert.csv')

# Concatenate the DataFrames along the columns (axis=1)
combined_df = pd.concat([tfidf_df, word2vec_df.drop(["y_true"], axis=1), glove_df.drop(["y_true"], axis=1), albert_df.drop(["y_true"], axis=1)], axis=1)

# Optionally, save the combined DataFrame to a new CSV file
# combined_df.to_csv('Phase1/Combined.csv', index=False)

# Display the combined DataFrame
combined_df.head()


y_true   class_0   class_1   class_2   class_3   class_4   class_5  \
0       2  0.004856  0.009864  0.864422  0.008940  0.009183  0.016639   
1       2  0.005297  0.006558  0.913401  0.006262  0.011597  0.018983   
2       2  0.030078  0.035363  0.681136  0.038987  0.025477  0.060935   
3       2  0.014440  0.015472  0.790973  0.023952  0.023529  0.020345   
4       2  0.012646  0.019750  0.612334  0.116218  0.036532  0.027983   

    class_6   class_7   class_8  ...       class_0       class_1   class_2  \
0  0.039277  0.026571  0.010824  ...  4.046189e-06  1.673384e-06  0.996728   
1  0.018909  0.006744  0.009302  ...  2.162968e-07  8.667423e-07  0.999940   
2  0.024796  0.033198  0.045627  ...  1.016335e-04  3.334410e-04  0.998280   
3  0.037677  0.027091  0.030567  ...  1.920308e-03  1.006953e-02  0.955455   
4  0.045918  0.060600  0.036102  ...  2.279302e-04  3.630354e-05  0.944598   

        class_3   class_4   class_5       class_6       class_7   class_8  \
0  8.242731e-04  0.002150  0.000016  2.555716e-07  8.192644e-05  0.000194   
1  3.937645e-07  0.000004  0.000004  6.603543e-08  2.003625e-07  0.000051   
2  5.001128e-05  0.000006  0.000730  2.283566e-07  1.428000e-06  0.000497   
3  2.492423e-03  0.006655  0.000183  3.224371e-04  1.568429e-02  0.006673   
4  4.439209e-02  0.002457  0.000046  6.339463e-06  7.960528e-03  0.000233   

        class_9  
0  8.416093e-09  
1  2.772808e-09  
2  7.577643e-07  
3  5.461269e-04  
4  4.337906e-05  

[5 rows x 41 columns]

In [42]:
combined_df.to_csv('Phase1/Combined.csv', index=False)

In [43]:
len(combined_df)

35251

In [44]:
X = combined_df.drop(["y_true"], axis =1 )
y = combined_df["y_true"]

In [45]:
from models import *
print("Logistic Regression:")
report, acc = logistic_regression(X, y)
print("Accuracy:", acc)
print(report)

print("\nDecision Tree Classifier:")
report, acc = decision_tree(X, y)
print("Accuracy:", acc)
print(report)

print("\nRandom Forest Classifier:")
report, acc = random_forest(X, y)
print("Accuracy:", acc)
print(report)

print("\nSupport Vector Machine (SVM):")
report, acc = support_vector_machine(X, y)
print("Accuracy:", acc)
print(report)

print("\nk-Nearest Neighbors (k-NN):")
report, acc = knn(X, y, k=5)
print("Accuracy:", acc)
print(report)

print("\nNaïve Bayes Classifier:")
report, acc = naive_bayes(X, y)
print("Accuracy:", acc)
print(report)

# print("\nGradient Boosting (XGBoost):")
# report, acc = xgboost_classifier(X, y)
# print("Accuracy:", acc)
# print(report)

# print("\nMulti-Layer Perceptron (MLP - Neural Network):")
# report, acc = mlp_classifier(X, y)

# print("Accuracy:", acc)
# print(report)


Logistic Regression:
Accuracy: 0.7984683023684583
              precision    recall  f1-score   support

           0       0.76      0.79      0.77       792
           1       0.69      0.71      0.70       709
           2       0.84      0.82      0.83       729
           3       0.76      0.88      0.82       830
           4       0.84      0.74      0.79       486
           5       0.87      0.88      0.88       680
           6       0.96      0.98      0.97       803
           7       0.71      0.66      0.68       634
           8       0.70      0.57      0.63       704
           9       0.83      0.88      0.86       684

    accuracy                           0.80      7051
   macro avg       0.80      0.79      0.79      7051
weighted avg       0.80      0.80      0.80      7051


Decision Tree Classifier:


/home/darth/.pyenv/versions/major02/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1247: FutureWarning: 'multi_class' was deprecated in version 1.5 and will be removed in 1.7. From then on, it will always use 'multinomial'. Leave it to its default value to avoid this warning.
  warnings.warn(


Accuracy: 0.4355410580059566
              precision    recall  f1-score   support

           0       0.56      0.52      0.54       792
           1       0.43      0.39      0.41       709
           2       0.34      0.33      0.34       729
           3       0.44      0.50      0.47       830
           4       0.52      0.31      0.39       486
           5       0.33      0.46      0.39       680
           6       0.54      0.68      0.60       803
           7       0.33      0.34      0.34       634
           8       0.29      0.27      0.28       704
           9       0.68      0.46      0.55       684

    accuracy                           0.44      7051
   macro avg       0.45      0.43      0.43      7051
weighted avg       0.45      0.44      0.43      7051


Random Forest Classifier:
Accuracy: 0.5664444759608566
              precision    recall  f1-score   support

           0       0.51      0.57      0.54       792
           1       0.37      0.35      0.36    